# PROGRES - TME2

In [1]:
import re
import xml.etree.ElementTree as ET
import json
import csv
import requests
from bs4 import BeautifulSoup as bs
from bottle import *

## Exercice 1 - Expressions régulières

1. Utiliser les expressions régulières pour identifier les adresses gmail valides et les afficher.

In [2]:
def is_valid_gmail(mail):
    pattern = '^[a-zA-Z0-9]+[\._]?[a-zA-Z0-9]+@gmail\.com'
    m = re.match(pattern, mail)
    if m is None:
        return False
    else:
        return True

In [3]:
is_valid_gmail("ab.@gmail.com")

False

In [4]:
is_valid_gmail("marie.Dupond@gmail.com")

True

In [5]:
is_valid_gmail("lucie.Durand@wanadoo.fr")

False

In [6]:
is_valid_gmail("Sophie.Parmentier@@gmail.com")

False

In [7]:
is_valid_gmail("franck.Dupres.gmail.com")

False

In [8]:
is_valid_gmail("pierre.Martin@lip6.fr")

False

In [9]:
is_valid_gmail("eric.Deschamps@gmail.com")

True

2. Utiliser les expressions régulières  pour vérifier si une chaine de caractères se termine par un chiffre.

In [10]:
def end_digit(string):
    m = re.match('.{0,}[0-9]{1}', string)
    if m:
        return True
    else:
        return False

In [11]:
end_digit("adrien9")

True

In [12]:
end_digit("adrien")

False

In [13]:
end_digit("9")

True

In [14]:
end_digit("adrien09")

True

3. Utiliser les expressions régulières pour supprimer les zéros problématiques dans une addresse IPv4 exprimée sous la forme d'une chaine de caractères.

__Exemple__:
- 216.08.094.196 devient 216.8.94.196
- 216.80.140.196 reste 216.80.140.196

In [15]:
def reset_number(number):
    if number in ["0", "00", "000"]:
        return "0"
    m = re.match('([0-9])([0-9])([0-9]){0,1}', number)
    l = []
    if m.group(1) != "0":
        # le premier chiffre n'est pas un 0
        l.append(m.group(1))
        try:
            # le premier chiffre n'étant pas un 0,
            # je copie tous les autres chiffres
            l.append(m.group(2))
            l.append(m.group(3))
        except IndexError:
            pass
    else:
        # le premier chiffre est un 0
        try:
            if m.group(2) != "0":
                # le deuxième chiffre n'est pas un 0
                l.append(m.group(2))
                try:
                    l.append(m.group(3))
                except IndexError:
                    pass
            else:
                # le deuxième chiffre est un 0
                # donc le troisième n'est forcément pas un 0
                l.append(m.group(3))
        except IndexError:
            pass
    try:
        l.remove(None)
    except ValueError:
        pass
    return "".join(l)

In [16]:
def rewrite_ip(ip):
    m = re.match('([0-9]+)\.([0-9]+)\.([0-9]+)\.([0-9]+)', ip)
    return ".".join([reset_number(m.group(1)), reset_number(m.group(2)),
                    reset_number(m.group(3)), reset_number(m.group(4))])

In [17]:
rewrite_ip("216.008.094.196")

'216.8.94.196'

In [18]:
rewrite_ip("216.80.140.196")

'216.80.140.196'

4. Utiliser les expressios régulières pour transformer une date au format MM-DD-YYYY vers le format DD-MM-YYYY.

__Exemple__:
- 11-06-2020 devient 06-11-2020

In [19]:
def rewrite_date(da):
    m = re.match('([0-9]{1,2})\-([0-9]{1,2})\-([0-9]{4})', da)
    return f"{m.group(2)}-{m.group(1)}-{m.group(3)}"

In [20]:
rewrite_date("11-06-2020")

'06-11-2020'

## Exercice 2 - Analyser du XML

Ecrire un programme Python qui va:

1. Récupérer le contenu de la page à l'adresse : [https://www.w3schools.com/xml/cd_catalog.xml]

In [21]:
r = requests.get("https://www.w3schools.com/xml/cd_catalog.xml")
with open("cd_catalog.xml", 'wb') as f:
    f.write(r.text.encode('utf-8'))

In [22]:
tree = ET.parse('cd_catalog.xml')
root = tree.getroot()

2. Afficher pour les CD: le titre, l'artiste, le pays, la compagnie, l'année

In [23]:
for cd in root:
    print("---cd")
    for elem in cd:
        if elem.tag in ["TITLE", "ARTIST", "COUNTRY", "COMPANY", "YEAR"]:
            print(" |---- " + str(elem.tag) + ": " + elem.text)
    print(" |")

---cd
 |---- TITLE: Empire Burlesque
 |---- ARTIST: Bob Dylan
 |---- COUNTRY: USA
 |---- COMPANY: Columbia
 |---- YEAR: 1985
 |
---cd
 |---- TITLE: Hide your heart
 |---- ARTIST: Bonnie Tyler
 |---- COUNTRY: UK
 |---- COMPANY: CBS Records
 |---- YEAR: 1988
 |
---cd
 |---- TITLE: Greatest Hits
 |---- ARTIST: Dolly Parton
 |---- COUNTRY: USA
 |---- COMPANY: RCA
 |---- YEAR: 1982
 |
---cd
 |---- TITLE: Still got the blues
 |---- ARTIST: Gary Moore
 |---- COUNTRY: UK
 |---- COMPANY: Virgin records
 |---- YEAR: 1990
 |
---cd
 |---- TITLE: Eros
 |---- ARTIST: Eros Ramazzotti
 |---- COUNTRY: EU
 |---- COMPANY: BMG
 |---- YEAR: 1997
 |
---cd
 |---- TITLE: One night only
 |---- ARTIST: Bee Gees
 |---- COUNTRY: UK
 |---- COMPANY: Polydor
 |---- YEAR: 1998
 |
---cd
 |---- TITLE: Sylvias Mother
 |---- ARTIST: Dr.Hook
 |---- COUNTRY: UK
 |---- COMPANY: CBS
 |---- YEAR: 1973
 |
---cd
 |---- TITLE: Maggie May
 |---- ARTIST: Rod Stewart
 |---- COUNTRY: UK
 |---- COMPANY: Pickwick
 |---- YEAR: 1990
 |


3. Afficher tous les CD des années 1980

In [24]:
for cd in root:
    is_year80 = False
    result = "---cd\n"
    for elem in cd:
        result += " |---" + elem.text + "\n"
        if elem.tag == "YEAR" and 1980 <= int(elem.text) <= 1989:
            is_year80 = True
    if is_year80:
        print(f"{result} |")

---cd
 |---Empire Burlesque
 |---Bob Dylan
 |---USA
 |---Columbia
 |---10.90
 |---1985
 |
---cd
 |---Hide your heart
 |---Bonnie Tyler
 |---UK
 |---CBS Records
 |---9.90
 |---1988
 |
---cd
 |---Greatest Hits
 |---Dolly Parton
 |---USA
 |---RCA
 |---9.90
 |---1982
 |
---cd
 |---When a man loves a woman
 |---Percy Sledge
 |---USA
 |---Atlantic
 |---8.70
 |---1987
 |
---cd
 |---Stop
 |---Sam Brown
 |---UK
 |---A and M
 |---8.90
 |---1988
 |
---cd
 |---Bridge of Spies
 |---T'Pau
 |---UK
 |---Siren
 |---7.90
 |---1987
 |
---cd
 |---Private Dancer
 |---Tina Turner
 |---UK
 |---Capitol
 |---8.90
 |---1983
 |
---cd
 |---Midt om natten
 |---Kim Larsen
 |---EU
 |---Medley
 |---7.80
 |---1983
 |
---cd
 |---Picture book
 |---Simply Red
 |---EU
 |---Elektra
 |---7.20
 |---1985
 |
---cd
 |---Red
 |---The Communards
 |---UK
 |---London
 |---7.80
 |---1987
 |
---cd
 |---Unchain my heart
 |---Joe Cocker
 |---USA
 |---EMI
 |---8.20
 |---1987
 |


4. Afficher tous les CD anglais

In [25]:
for cd in root:
    is_uk = False
    result = "---cd\n"
    for elem in cd:
        result += " |----" + elem.text + "\n"
        if elem.tag == "COUNTRY" and elem.text == "UK":
            is_uk = True
    if is_uk:
        print(f"{result} |")

---cd
 |----Hide your heart
 |----Bonnie Tyler
 |----UK
 |----CBS Records
 |----9.90
 |----1988
 |
---cd
 |----Still got the blues
 |----Gary Moore
 |----UK
 |----Virgin records
 |----10.20
 |----1990
 |
---cd
 |----One night only
 |----Bee Gees
 |----UK
 |----Polydor
 |----10.90
 |----1998
 |
---cd
 |----Sylvias Mother
 |----Dr.Hook
 |----UK
 |----CBS
 |----8.10
 |----1973
 |
---cd
 |----Maggie May
 |----Rod Stewart
 |----UK
 |----Pickwick
 |----8.50
 |----1990
 |
---cd
 |----For the good times
 |----Kenny Rogers
 |----UK
 |----Mucik Master
 |----8.70
 |----1995
 |
---cd
 |----Tupelo Honey
 |----Van Morrison
 |----UK
 |----Polydor
 |----8.20
 |----1971
 |
---cd
 |----The very best of
 |----Cat Stevens
 |----UK
 |----Island
 |----8.90
 |----1990
 |
---cd
 |----Stop
 |----Sam Brown
 |----UK
 |----A and M
 |----8.90
 |----1988
 |
---cd
 |----Bridge of Spies
 |----T'Pau
 |----UK
 |----Siren
 |----7.90
 |----1987
 |
---cd
 |----Private Dancer
 |----Tina Turner
 |----UK
 |----Capitol
 |----

## Exercice 3 - Analyser du JSON

Ecrire un programme Python qui va:

1. Récupérer le fichier des lieux de tournage à Paris à l'adresse: [https://opendata.paris.fr/explore/dataset/lieux-de-tournage-a-paris/download/?format=json&timezone=Europe/Berlin&lang=fr]

In [1]:
r = requests.get("https://opendata.paris.fr/explore/dataset/lieux-de-tournage-a-paris/download/?format=json&timezone=Europe/Berlin&lang=fr")
with open("lieux_tournage_paris.txt", 'wb') as f:
    f.write(r.text.encode('utf-8'))

NameError: name 'requests' is not defined

2. Analyser le fichier JSON obtenu pour afficher, pour toutes les entrées: le réalisateur, le titre, l'arrondissement, la date de début, la date de fin, les coordonnées géographiques.

In [27]:
with open("lieux_tournage_paris.txt") as infile:
    data = json.load(infile)
    for p in data:
        result = "---tournage\n"
        s = p['fields']
        for k in s.keys():
            if k == "nom_producteur":
                result += " |----Réalisateur: " + s[k] + "\n"
            elif k == "nom_tournage":
                result += " |----Titre: " + s[k] + "\n"
            elif k == "ardt_lieu":
                result += " |----Arrondissement: " + s[k] + "\n"
            elif k == "date_debut":
                result += " |----Date de début: " + s[k] + "\n"
            elif k == "date_fin":
                result += " |----Date de fin: " + s[k] + "\n"
            elif k == "coord_x":
                result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
            elif k == "coord_y":
                result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
        print(result)
                

---tournage
 |----Coordonnées géographique X: 48.86260438
 |----Coordonnées géographique X: 2.27389054
 |----Date de fin: 2018-11-08
 |----Réalisateur: LA VERITE PRODUCTION
 |----Titre: LA VERITE SI JE MENS LES DEBUTS
 |----Date de début: 2018-11-08
 |----Arrondissement: 75116

---tournage
 |----Coordonnées géographique X: 48.8734189
 |----Coordonnées géographique X: 2.38225633
 |----Date de fin: 2019-06-18
 |----Réalisateur: C.S. Productions
 |----Titre: Maoussi
 |----Date de début: 2019-06-18
 |----Arrondissement: 75019

---tournage
 |----Coordonnées géographique X: 48.86894539
 |----Coordonnées géographique X: 2.39045793
 |----Date de fin: 2019-06-18
 |----Réalisateur: C.S. Productions
 |----Titre: Maoussi
 |----Date de début: 2019-06-18
 |----Arrondissement: 75020

---tournage
 |----Coordonnées géographique X: 48.87009523
 |----Coordonnées géographique X: 2.32904348
 |----Date de fin: 2019-06-12
 |----Réalisateur: GAUMONT
 |----Titre: TOUT SIMPLEMENT NOIR
 |----Date de début: 2019-


---tournage
 |----Coordonnées géographique X: 48.88981513
 |----Coordonnées géographique X: 2.34290313
 |----Date de fin: 2018-10-17
 |----Réalisateur: BOXEUR 7
 |----Titre: CANDICE RENOIR SAISON 7 Ep 62-63-64
 |----Date de début: 2018-10-17
 |----Arrondissement: 75018

---tournage
 |----Coordonnées géographique X: 48.861863
 |----Coordonnées géographique X: 2.338081
 |----Date de fin: 2016-01-30
 |----Réalisateur: FIRSTEP
 |----Titre: WAR MACHINE
 |----Date de début: 2016-01-30
 |----Arrondissement: 75001

---tournage
 |----Coordonnées géographique X: 48.853542
 |----Coordonnées géographique X: 2.3472210000000002
 |----Date de fin: 2016-04-26
 |----Réalisateur: FIRSTEP
 |----Titre: BEFIKRE
 |----Date de début: 2016-04-26
 |----Arrondissement: 75004

---tournage
 |----Coordonnées géographique X: 48.867616
 |----Coordonnées géographique X: 2.350652
 |----Date de fin: 2016-11-23
 |----Réalisateur: NOLITA CINEMA
 |----Titre: LEILA
 |----Date de début: 2016-11-22
 |----Arrondissement: 750


---tournage
 |----Coordonnées géographique X: 48.84370967
 |----Coordonnées géographique X: 2.38316151
 |----Date de fin: 2019-07-11
 |----Réalisateur: RECTANGLE PRODUCTIONS
 |----Titre: PARENT D'ELEVE
 |----Date de début: 2019-07-11
 |----Arrondissement: 75012

---tournage
 |----Coordonnées géographique X: 48.847329
 |----Coordonnées géographique X: 2.347565
 |----Date de fin: 2016-02-18
 |----Réalisateur: LES PRODUCTIONS DU TRESOR
 |----Titre: GC5
 |----Date de début: 2016-02-18
 |----Arrondissement: 75005

---tournage
 |----Coordonnées géographique X: 48.851314
 |----Coordonnées géographique X: 2.380487
 |----Date de fin: 2016-11-14
 |----Réalisateur: MY FAMILY
 |----Titre: LOUE MOI
 |----Date de début: 2016-11-14
 |----Arrondissement: 75011

---tournage
 |----Coordonnées géographique X: 48.88007557
 |----Coordonnées géographique X: 2.35732163
 |----Date de fin: 2019-07-24
 |----Réalisateur: NW2020
 |----Titre: Hanna 2
 |----Date de début: 2019-07-23
 |----Arrondissement: 75010

--


---tournage
 |----Coordonnées géographique X: 48.8755623
 |----Coordonnées géographique X: 2.32536654
 |----Date de fin: 2020-09-14
 |----Réalisateur: Novoprod
 |----Titre: Être En Mouvement
 |----Date de début: 2020-09-14
 |----Arrondissement: 75008

---tournage
 |----Coordonnées géographique X: 48.88606874
 |----Coordonnées géographique X: 2.37303226
 |----Date de fin: 2020-09-18
 |----Réalisateur: Unité
 |----Titre: Entre les Vagues
 |----Date de début: 2020-09-17
 |----Arrondissement: 75019

---tournage
 |----Coordonnées géographique X: 48.88145471
 |----Coordonnées géographique X: 2.3736886200000002
 |----Date de fin: 2020-09-22
 |----Réalisateur: AUTHENTIC PROD
 |----Titre: SAM SAISON 5
 |----Date de début: 2020-09-21
 |----Arrondissement: 75019

---tournage
 |----Coordonnées géographique X: 48.88065795
 |----Coordonnées géographique X: 2.3925515
 |----Date de fin: 2019-01-26
 |----Réalisateur: MERLIN PRODUCTIONS
 |----Titre: CLEM
 |----Date de début: 2019-01-21
 |----Arrondisse

In [28]:
with open("lieux_tournage_paris.txt") as infile:
    data = json.load(infile)
    for p in data:
        #result = "---tournage\n"
        s = p['fields']
        for k in s.keys():
            if k == "nom_producteur":
                rea = s[k]
                #result += " |----Réalisateur: " + s[k] + "\n"
            elif k == "nom_tournage":
                tt = s[k]
                #result += " |----Titre: " + s[k] + "\n"
            elif k == "ardt_lieu":
                arr = s[k]
                #result += " |----Arrondissement: " + s[k] + "\n"
            elif k == "date_debut":
                dd = s[k]
                #result += " |----Date de début: " + s[k] + "\n"
            elif k == "date_fin":
                df = s[k]
                #result += " |----Date de fin: " + s[k] + "\n"
            elif k == "coord_x":
                cgx = s[k]
                #result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
            elif k == "coord_y":
                cgy = s[k]
                #result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
        #print(result)
        print(f"""---tournage
 |----Réalisateur: {rea}
 |----Titre: {tt}
 |----Arrondissement: {arr}
 |----Date de début: {dd}
 |----Date de fin: {df}
 |----Coordonnées géographique: x = {cgx}, y = {cgy}
 """)

---tournage
 |----Réalisateur: LA VERITE PRODUCTION
 |----Titre: LA VERITE SI JE MENS LES DEBUTS
 |----Arrondissement: 75116
 |----Date de début: 2018-11-08
 |----Date de fin: 2018-11-08
 |----Coordonnées géographique: x = 2.27389054, y = 48.86260438
 
---tournage
 |----Réalisateur: C.S. Productions
 |----Titre: Maoussi
 |----Arrondissement: 75019
 |----Date de début: 2019-06-18
 |----Date de fin: 2019-06-18
 |----Coordonnées géographique: x = 2.38225633, y = 48.8734189
 
---tournage
 |----Réalisateur: C.S. Productions
 |----Titre: Maoussi
 |----Arrondissement: 75020
 |----Date de début: 2019-06-18
 |----Date de fin: 2019-06-18
 |----Coordonnées géographique: x = 2.39045793, y = 48.86894539
 
---tournage
 |----Réalisateur: GAUMONT
 |----Titre: TOUT SIMPLEMENT NOIR
 |----Arrondissement: 75009
 |----Date de début: 2019-06-12
 |----Date de fin: 2019-06-12
 |----Coordonnées géographique: x = 2.32904348, y = 48.87009523
 
---tournage
 |----Réalisateur: ALTER FILMS - CHACUN CHEZ SOI !
 |----

---tournage
 |----Réalisateur: Page 114
 |----Titre: Les Olympiades
 |----Arrondissement: 75013
 |----Date de début: 2020-10-02
 |----Date de fin: 2020-10-03
 |----Coordonnées géographique: x = 2.36223267, y = 48.82654854
 
---tournage
 |----Réalisateur: EX NIHILO
 |----Titre: Les Jeunes Amants
 |----Arrondissement: 75019
 |----Date de début: 2020-10-23
 |----Date de fin: 2020-10-23
 |----Coordonnées géographique: x = 2.38095049, y = 48.87595938
 
---tournage
 |----Réalisateur: BIG BAND STORY
 |----Titre: COUP DE FOUDRE A JAIPUR
 |----Arrondissement: 75008
 |----Date de début: 2016-03-31
 |----Date de fin: 2016-03-31
 |----Coordonnées géographique: x = 2.319739, y = 48.87842
 
---tournage
 |----Réalisateur: AGAT FILMS
 |----Titre: UN TRIOMPHE
 |----Arrondissement: 75006
 |----Date de début: 2019-12-19
 |----Date de fin: 2019-12-21
 |----Coordonnées géographique: x = 2.33900999, y = 48.84997162
 
---tournage
 |----Réalisateur: Gaumont Production Télévision
 |----Titre: PLAN B
 |----Arro

---tournage
 |----Réalisateur: VVZ
 |----Titre: EIFFEL
 |----Arrondissement: 75007
 |----Date de début: 2019-09-03
 |----Date de fin: 2019-09-05
 |----Coordonnées géographique: x = 2.29590088, y = 48.85452819
 
---tournage
 |----Réalisateur: DAY FOR NIGHT
 |----Titre: PARIS, LA BLANCHE
 |----Arrondissement: 75018
 |----Date de début: 2016-02-22
 |----Date de fin: 2016-02-22
 |----Coordonnées géographique: x = 2.331789, y = 48.884207
 
---tournage
 |----Réalisateur: DIAPHANA FILMS
 |----Titre: Par-dessus l'épaule de Jonas
 |----Arrondissement: 75017
 |----Date de début: 2019-09-05
 |----Date de fin: 2019-09-05
 |----Coordonnées géographique: x = 2.30105919, y = 48.89232908
 
---tournage
 |----Réalisateur: TABO TABO FILMS
 |----Titre: NUMERO UNE
 |----Arrondissement: 75008
 |----Date de début: 2016-11-04
 |----Date de fin: 2016-11-05
 |----Coordonnées géographique: x = 2.297694, y = 48.874211
 
---tournage
 |----Réalisateur: VVZ
 |----Titre: EIFFEL
 |----Arrondissement: 75116
 |----Date 

---tournage
 |----Réalisateur: LES FILMS DE PIERRE
 |----Titre: ARTHUR RAMBO
 |----Arrondissement: 75020
 |----Date de début: 2019-10-03
 |----Date de fin: 2019-10-03
 |----Coordonnées géographique: x = 2.41267398, y = 48.85754085
 
---tournage
 |----Réalisateur: MOBY DICK FILMS
 |----Titre: LES CHOSES QU'ON DIT, LES CHOSES QU'ON FAIT
 |----Arrondissement: 75002
 |----Date de début: 2019-11-04
 |----Date de fin: 2019-11-05
 |----Coordonnées géographique: x = 2.34604247, y = 48.86659312
 
---tournage
 |----Réalisateur: KWAI
 |----Titre: SERIE BARON NOIR SAISON 3
 |----Arrondissement: 75116
 |----Date de début: 2019-10-09
 |----Date de fin: 2019-10-09
 |----Coordonnées géographique: x = 2.29713577, y = 48.86627187
 
---tournage
 |----Réalisateur: legendaire
 |----Titre: J'ACCUSE
 |----Arrondissement: 75007
 |----Date de début: 2018-11-26
 |----Date de fin: 2018-11-26
 |----Coordonnées géographique: x = 2.31856095, y = 48.85964034
 
---tournage
 |----Réalisateur: DE L'AUTRE COTE DU DU PER

3. Afficher pour chaque film (il peut y avoir plusieurs entrées pour un meme film) le réalisateur, les dates de tournage, et les lieux.

In [29]:
with open("lieux_tournage_paris.txt") as infile:
    data = json.load(infile)
    results = {}
    for p in data:
        s = p['fields']
        for k in s.keys():
            if k == "nom_producteur":
                rea = s[k]
                #result += " |----Réalisateur: " + s[k] + "\n"
            elif k == "nom_tournage":
                tt = s[k]
                #result += " |----Titre: " + s[k] + "\n"
            elif k == "ardt_lieu":
                arr = s[k]
                #result += " |----Arrondissement: " + s[k] + "\n"
            elif k == "date_debut":
                dd = s[k]
                #result += " |----Date de début: " + s[k] + "\n"
            elif k == "date_fin":
                df = s[k]
                #result += " |----Date de fin: " + s[k] + "\n"
            elif k == "coord_x":
                cgx = s[k]
                #result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
            elif k == "coord_y":
                cgy = s[k]
                #result += " |----Coordonnées géographique X: " + str(s[k]) + "\n"
        if tt in results.keys():
            r_s = results[tt]
            new_r = {"arr": arr, "dd": dd, "df": df, "cg": (cgx, cgy)}
            r_s["infos"].append(new_r)
        else:
            new_r = {"arr": arr, "dd": dd, "df": df, "cg": (cgx, cgy)}
            r_s = {"rea": rea, "tt": tt, "infos": [new_r]}
            results[tt] = r_s
    for k in results.keys():
        result = results[k]
        result_infos = result['infos']
        print(f"""---tournage
 |----Réalisateur: {result['rea']}
 |----Titre: {result['tt']}
 |---- other infos:""")
        for elem in result_infos:
            print(f"""    |----Arrondissement: {elem['arr']}
    |----Date de début: {elem['dd']}
    |----Date de fin: {elem['df']}
    |----Coordonnées géographique: {elem['cg']}
""")
    print()

---tournage
 |----Réalisateur: LA VERITE PRODUCTION
 |----Titre: LA VERITE SI JE MENS LES DEBUTS
 |---- other infos:
    |----Arrondissement: 75116
    |----Date de début: 2018-11-08
    |----Date de fin: 2018-11-08
    |----Coordonnées géographique: (2.27389054, 48.86260438)

    |----Arrondissement: 75010
    |----Date de début: 2018-10-01
    |----Date de fin: 2018-10-03
    |----Coordonnées géographique: (2.3679667, 48.87149251)

    |----Arrondissement: 75116
    |----Date de début: 2018-11-16
    |----Date de fin: 2018-11-17
    |----Coordonnées géographique: (2.29340346, 48.86858858)

    |----Arrondissement: 75002
    |----Date de début: 2018-10-08
    |----Date de fin: 2018-10-08
    |----Coordonnées géographique: (2.35134099, 48.867125)

    |----Arrondissement: 75116
    |----Date de début: 2018-11-16
    |----Date de fin: 2018-11-17
    |----Coordonnées géographique: (2.29265813, 48.86819003)

    |----Arrondissement: 75014
    |----Date de début: 2018-10-09
    |----Date d

    |----Arrondissement: 75019
    |----Date de début: 2019-07-17
    |----Date de fin: 2019-07-18
    |----Coordonnées géographique: (2.40629851, 48.87727215)

    |----Arrondissement: 75019
    |----Date de début: 2019-07-17
    |----Date de fin: 2019-07-19
    |----Coordonnées géographique: (2.39324502, 48.88213597)

    |----Arrondissement: 75003
    |----Date de début: 2019-07-12
    |----Date de fin: 2019-07-12
    |----Coordonnées géographique: (2.3655342, 48.8563274)

    |----Arrondissement: 75009
    |----Date de début: 2019-07-16
    |----Date de fin: 2019-07-16
    |----Coordonnées géographique: (2.33187457, 48.8710898)

    |----Arrondissement: 75005
    |----Date de début: 2019-06-27
    |----Date de fin: 2019-06-27
    |----Coordonnées géographique: (2.34853376, 48.84753693)

    |----Arrondissement: 75009
    |----Date de début: 2019-06-18
    |----Date de fin: 2019-06-18
    |----Coordonnées géographique: (2.34676119, 48.87397923)

    |----Arrondissement: 75004
    |-


    |----Arrondissement: 75016
    |----Date de début: 2016-12-14
    |----Date de fin: 2016-12-14
    |----Coordonnées géographique: (2.294048, 48.864589)

    |----Arrondissement: 75018
    |----Date de début: 2016-12-15
    |----Date de fin: 2016-12-15
    |----Coordonnées géographique: (2.340453, 48.888563)

    |----Arrondissement: 75018
    |----Date de début: 2016-12-15
    |----Date de fin: 2016-12-15
    |----Coordonnées géographique: (2.340672, 48.887612)

    |----Arrondissement: 75004
    |----Date de début: 2016-12-13
    |----Date de fin: 2016-12-13
    |----Coordonnées géographique: (2.351419, 48.859772)

    |----Arrondissement: 75018
    |----Date de début: 2016-12-15
    |----Date de fin: 2016-12-15
    |----Coordonnées géographique: (2.340543, 48.886576)

    |----Arrondissement: 75006
    |----Date de début: 2016-12-12
    |----Date de fin: 2016-12-12
    |----Coordonnées géographique: (2.336771, 48.852798)

    |----Arrondissement: 75006
    |----Date de début: 20


    |----Arrondissement: 75008
    |----Date de début: 2016-08-19
    |----Date de fin: 2016-08-19
    |----Coordonnées géographique: (2.313053, 48.878944)

    |----Arrondissement: 75006
    |----Date de début: 2016-08-25
    |----Date de fin: 2016-08-25
    |----Coordonnées géographique: (2.334578, 48.852046)

    |----Arrondissement: 75006
    |----Date de début: 2016-08-26
    |----Date de fin: 2016-08-26
    |----Coordonnées géographique: (2.341605, 48.855171)

    |----Arrondissement: 75004
    |----Date de début: 2016-09-06
    |----Date de fin: 2016-09-06
    |----Coordonnées géographique: (2.3537150000000002, 48.860043)

    |----Arrondissement: 75017
    |----Date de début: 2016-09-07
    |----Date de fin: 2016-09-07
    |----Coordonnées géographique: (2.32866, 48.899266)

    |----Arrondissement: 75004
    |----Date de début: 2016-09-06
    |----Date de fin: 2016-09-06
    |----Coordonnées géographique: (2.353172, 48.860372)

    |----Arrondissement: 75019
    |----Date de 

4. Afficher pour chaque arrondissement son nombre de tournages.

In [30]:
# si un meme film a été tourné 2 fois sur le meme arrondissement
# il est compté comme un ou comme 2 ???
with open("lieux_tournage_paris.txt") as infile:
    data = json.load(infile)
    results = {}
    for p in data:
        s = p['fields']
        for k in s.keys():
            if k == "nom_tournage":
                if s[k] in results.keys():
                    results[s[k]] += 1
                else:
                    results[s[k]] = 1
    for k in results.keys():
        print(f"---> {k} : {results[k]}")

---> LA VERITE SI JE MENS LES DEBUTS : 10
---> Maoussi : 18
---> TOUT SIMPLEMENT NOIR : 37
---> CHACUN CHEZ SOI ! : 9
---> ENGRENAGES SAISON 8 : 43
---> Une sirène à Paris : 15
---> HORS NORMES : 22
---> LE MEILLEUR RESTE À VENIR : 18
---> La nuit, je mens... : 31
---> Le Lion : 12
---> ROMANCE : 14
---> De l'or pour les chiens : 21
---> CANTABILE YOUTH : 13
---> The Eddy : 59
---> Seize Printemps : 27
---> SERIE BARON NOIR SAISON 3 : 12
---> Emily in Paris : 87
---> SKAM SAISON 5 ET 6 SEMAINE 2 SUR 9 : 8
---> SMILEY : 6
---> TANGUY 2 : 26
---> CLEM SAISON 9 : 1
---> It Must Be Heaven : 20
---> FORTE : 33
---> FAMILY BUSINESS S1 : 19
---> Rétro : 9
---> PAR UN DEMI CLAIR MATIN : 13
---> LE MENSONGE : 1
---> C'EST QUOI CETTE FAMILLE?! 2 : 1
---> Munch  saison 2 : 21
---> LE PRINCE OUBLIE : 2
---> PLACE DES VICTOIRES : 21
---> TOI, TOI, MON TOIT : 4
---> Madame Claude : 16
---> Comment je suis devenu Super Héros : 12
---> LES DEUX ALFRED : 12
---> Trois Fois Rien : 13
---> Mystère à la S

## Exercice 4 - Analyser du CSV

Ecrire un programme Python qui va:

1. Récupérer le fichier des titres les plus prétés dans les bibliothèques à Paris à l'adresse: [https://opendata.paris.fr/explore/dataset/les-titres-les-plus-pretes/download/?format=csv&timezone=Europe/Berlin&lang=fr&use_labels_for_header=true&csv_separator=%3B]

In [31]:
r = requests.get("https://opendata.paris.fr/explore/dataset/les-titres-les-plus-pretes/download/?format=csv&timezone=Europe/Berlin&lang=fr&use_labels_for_header=true&csv_separator=%3B")
with open("titres.cvs", 'wb') as f:
    f.write(r.text.encode('utf-8'))

2. Analyser le fichier CSV obtenu pour afficher, pour toutes les entrées: le titre, l'auteur, le nombre de prets.

In [32]:
with open('titres.cvs', newline='', encoding='utf-8') as csvfile:
    r = csv.DictReader(csvfile, delimiter=';', quotechar='|')
    for row in r:
        print(f"""---Livre
 |----Titre: {row['Titre']}
 |----Auteur: {row['Auteur']}
 |----Prêts: {row['Prêts']}
""")

<class 'csv.DictReader'>
---Livre
 |----Titre: Max et Lili ne font pas leurs devoirs
 |----Auteur: Saint-Mars, Dominique de
 |----Prêts: 886

---Livre
 |----Titre: Lili est stressée par la rentrée
 |----Auteur: Saint-Mars, Dominique de
 |----Prêts: 886

---Livre
 |----Titre: Max se fait insulter à la récré
 |----Auteur: Saint-Mars, Dominique de
 |----Prêts: 833

---Livre
 |----Titre: Max et Lili se posent des questions sur Dieu
 |----Auteur: Saint-Mars, Dominique de
 |----Prêts: 818

---Livre
 |----Titre: Journal infime
 |----Auteur: Neel, Julien
 |----Prêts: 781

---Livre
 |----Titre: Les Légendaires. 14. L'héritage du mal
 |----Auteur: Sobral, Patrick
 |----Prêts: 776

---Livre
 |----Titre: Les mabouls déboulent !
 |----Auteur: Cohen, Jaqueline
 |----Prêts: 764

---Livre
 |----Titre: Les Légendaires. 15. Amour mortel
 |----Auteur: Sobral, Patrick
 |----Prêts: 733

---Livre
 |----Titre: L'exode de Kalandre
 |----Auteur: Sobral, Patrick
 |----Prêts: 730

---Livre
 |----Titre: Versus in

3. Afficher pour chaque type de documents (il peut y avoir plusieurs entrées pour un meme type de documents), le nombre total de prets pour ce type.

In [33]:
with open('titres.cvs', newline='', encoding='utf-8') as csvfile:
    r = csv.DictReader(csvfile, delimiter=';', quotechar='|')
    print(type(r))
    first_line = True
    results = {}
    for row in r:
        if row['Type de document'] in results.keys():
            results[row['Type de document']] += int(row['Prêts'])
        else:
            results[row['Type de document']] = int(row['Prêts'])
    
    for tp in results.keys():
        print(f"""---Type de document: {tp}
 |----Nombre total de prêts: {results[tp]}
""")

<class 'csv.DictReader'>
---Type de document: Livre jeunesse
 |----Nombre total de prêts: 116591

---Type de document: Bande dessinée jeunesse
 |----Nombre total de prêts: 231530

---Type de document: Livre pour adulte
 |----Nombre total de prêts: 42255

---Type de document: Livre sonore jeunesse
 |----Nombre total de prêts: 6345

---Type de document: DVD jeunesse
 |----Nombre total de prêts: 18256

---Type de document: Jeux de société
 |----Nombre total de prêts: 475

---Type de document: Bande dessinée pour adulte
 |----Nombre total de prêts: 7308

---Type de document: Enregistrement musical pour la jeunesse
 |----Nombre total de prêts: 744

---Type de document: Jeux Vidéos tous publics
 |----Nombre total de prêts: 417



4. Afficher les titres dans l'ordre de rentabilité (par ordre décroissant du nombre de prets par exemplaire).

In [34]:
with open('titres.cvs', newline='', encoding='utf-8') as csvfile:
    r = csv.DictReader(csvfile, delimiter=';', quotechar='|')
    print(type(r))
    first_line = True
    results = {}
    for row in r:
        if row['Titre'] in results.keys():
            results[row['Titre']] += int(row['Prêts'])
        else:
            results[row['Titre']] = int(row['Prêts'])
            
    final_results = {}
    for tt in results.keys():
        if results[tt] in final_results.keys():
            final_results[results[tt]].append(tt)
        else:
            final_results[results[tt]] = [tt]
    
    sorted(final_results)
    for nb in final_results.keys():
        print(f"---Nombre total de prêts: {nb}")
        ll = final_results[nb]
        for elem in ll:
            print(f""" |----Titre: {elem}""")
        print()

<class 'csv.DictReader'>
---Nombre total de prêts: 886
 |----Titre: Max et Lili ne font pas leurs devoirs
 |----Titre: Lili est stressée par la rentrée

---Nombre total de prêts: 833
 |----Titre: Max se fait insulter à la récré

---Nombre total de prêts: 818
 |----Titre: Max et Lili se posent des questions sur Dieu

---Nombre total de prêts: 781
 |----Titre: Journal infime

---Nombre total de prêts: 776
 |----Titre: Les Légendaires. 14. L'héritage du mal

---Nombre total de prêts: 764
 |----Titre: Les mabouls déboulent !

---Nombre total de prêts: 733
 |----Titre: Les Légendaires. 15. Amour mortel
 |----Titre: Max est fou de jeux vidéo
 |----Titre: Lili n'aime que les frites
 |----Titre: Emilie n'aime pas quand sa mère boit trop

---Nombre total de prêts: 730
 |----Titre: L'exode de Kalandre
 |----Titre: Max ne veut pas se laver

---Nombre total de prêts: 690
 |----Titre: Versus inferno

---Nombre total de prêts: 678
 |----Titre: Max est casse-cou

---Nombre total de prêts: 646
 |----T

 |----Titre: L'épreuve de farce

---Nombre total de prêts: 533
 |----Titre: Dégâts à gogo !

---Nombre total de prêts: 499
 |----Titre: Couleurs de l'incendie

---Nombre total de prêts: 417
 |----Titre: Tablette Ipad : Parascolaire
 |----Titre: Fairy Tail. 57

---Nombre total de prêts: 378
 |----Titre: Fairy Tail. 59
 |----Titre: Fairy Tail. 55

---Nombre total de prêts: 995
 |----Titre: Lili invite une copine en vacances

---Nombre total de prêts: 788
 |----Titre: Main du futur

---Nombre total de prêts: 736
 |----Titre: Lili a la passion du cheval

---Nombre total de prêts: 712
 |----Titre: Les Légendaires. 16. L'éternité ne dure qu'un temps

---Nombre total de prêts: 706
 |----Titre: Quand sort la recluse

---Nombre total de prêts: 600
 |----Titre: La rose écarlate. 7. Tu seras toujours à moi

---Nombre total de prêts: 544
 |----Titre: Copain comme cochon

---Nombre total de prêts: 541
 |----Titre: Le chevalier cheval

---Nombre total de prêts: 526
 |----Titre: Un air de famille

--

## Exercice 5 - Analyser du HTML

Ecrire un programme Python qui va:

1. Récupérer le contenu de la page Wikipedia à l'adresse: [https://fr.wikipedia.org/wiki/Liste_des_pays_par_densit%c3%A9_de_population]

In [2]:
r = requests.get("https://fr.wikipedia.org/wiki/Liste_des_pays_par_densit%c3%A9_de_population")
with open("pays.html", 'wb') as f:
    f.write(r.text.encode('utf-8'))

2. Afficher tous les pays mentionnés dans le tableau <<Densité par pays (1950-2018)>>.

3. Afficher pour chaque pays son rang, sa densité, sa population, sa superficie.

4. Sauvegarder les informations obtenues dans un dictionnaire Python.

5. En utilisant le dictionnaire Python ainsi sauvegardé, demander à l'utilisateur un pays, lui afficher les informations correspondantes.

## Exercice 6 - API Web

1. Ecrire un programme Python qui va rendre disponible une API Web permettant des calculs élémentaires sur des nombres entiers. Les API sont accessibles par GET et de la forme:
- /add/{entier1}/{entier2} : réaliser l'addition de entier1 et entier2
- /sub/{entier1}/{entier2} : réaliser la soustraction de entier1 et entier2
- /mul/{entier1}/{entier2} : réaliser la multiplication de entier1 et entier2
- /div/{entier1}/{entier2} : réaliser la division entière de entier1 par entier2
- /mod/{entier1}/{entier2} : réalier le reste de la division entière de entier1 par entier2

In [ ]:
@route('/add/<entier1:int>/<entier2:int>', method='GET')
def add(entier1, entier2):
	return dumps(entier1 + entier2)


@route('/sub/<entier1:int>/<entier2:int>', method='GET')
def sub(entier1, entier2):
	return dumps(entier1 - entier2)


@route('/mul/<entier1:int>/<entier2:int>', method='GET')
def mul(entier1, entier2):
	return dumps(entier1 * entier2)


@route('/div/<entier1:int>/<entier2:int>', method='GET')
def div(entier1, entier2):
	return dumps(entier1 // entier2)


@route('/mod/<entier1:int>/<entier2:int>', method='GET')
def mod(entier1, entier2):
	return dumps(entier1 % entier2)


run(host='localhost', port=8080)


2. Ecrire un programme Python qui va tester l'API Web rendue disponible au moyen de la bibliothèque requests.

In [ ]:
from requests import *
from json import *
import unittest


class TestAPIMethods(unittest.TestCase):
	server_ip = 'localhost'
	server_port = 8080
	def test_add(self):
		r = get(f"http://{self.server_ip}:{self.server_port}/add/4/5")
		l = loads(r.text)
		self.assertEqual(l, 9)
		r = get(f"http://{self.server_ip}:{self.server_port}/add/-1/4")
		l = loads(r.text)
		self.assertEqual(l, 3)
		r = get(f"http://{self.server_ip}:{self.server_port}/add/1/-4")
		l = loads(r.text)
		self.assertEqual(l, -3)


	def test_sub(self):
		r = get(f"http://{self.server_ip}:{self.server_port}/sub/5/4")
		l = loads(r.text)
		self.assertEqual(l, 1)
		r = get(f"http://{self.server_ip}:{self.server_port}/sub/-1/4")
		l = loads(r.text)
		self.assertEqual(l, -5)
		r = get(f"http://{self.server_ip}:{self.server_port}/sub/1/-4")
		l = loads(r.text)
		self.assertEqual(l, 5)


	def test_mul(self):
		r = get(f"http://{self.server_ip}:{self.server_port}/mul/4/5")
		l = loads(r.text)
		self.assertEqual(l, 20)
		r = get(f"http://{self.server_ip}:{self.server_port}/mul/-1/4")
		l = loads(r.text)
		self.assertEqual(l, -4)
		r = get(f"http://{self.server_ip}:{self.server_port}/mul/1/-4")
		l = loads(r.text)
		self.assertEqual(l, -4)


	def test_div(self):
		r = get(f"http://{self.server_ip}:{self.server_port}/div/20/5")
		l = loads(r.text)
		self.assertEqual(l, 4)
		r = get(f"http://{self.server_ip}:{self.server_port}/div/23/5")
		l = loads(r.text)
		self.assertEqual(l, 4)
		r = get(f"http://{self.server_ip}:{self.server_port}/div/1/-4")
		l = loads(r.text)
		self.assertEqual(l, -1)
		# doit soulever une exception
		r = get(f"http://{self.server_ip}:{self.server_port}/div/4/0")


    def test_mod(self):
        r = get(f"http://{self.server_ip}:{self.server_port}/mod/20/5")
        l = loads(r.text)
        self.assertEqual(l, 0)
        r = get(f"http://{self.server_ip}:{self.server_port}/mod/23/5")
        l = loads(r.text)
        self.assertEqual(l, 3)
        r = get(f"http://{self.server_ip}:{self.server_port}/mod/1/-4")
        l = loads(r.text)
        self.assertEqual(l, -3)
        # doit soulever une exception
        r = get(f"http://{self.server_ip}:{self.server_port}/mod/4/0")


if __name__ == '__main__':
	unittest.main()